In [1]:
import numpy as np
# Train a model to classify real pulses vs. noise
import tensorflow as tf
from tensorflow.keras.layers import Input, LSTM, Dense
from tensorflow.keras.models import Model
import matplotlib.pyplot as plt
from sklearn.metrics import roc_curve, auc
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import average_precision_score
import awkward as ak
from tensorflow.keras.layers import Dropout
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.layers import GlobalAveragePooling1D, Embedding, MultiHeadAttention, Dense, Input, Dropout, LayerNormalization

In [2]:
num_events = 50000
num_samples = 10
xmin = 0
xmax = 10

In [3]:
# Generate data
np.random.seed(42)  # For reproducibility

def real_pulse(t):
    tmax = 6
    trise = 2.1287
    alpha = 1.0814
    pulse = np.power( (t-(tmax-trise))/trise, alpha ) * np.exp( -alpha*(t-tmax)/trise )
    zero_mask = np.where(t <= (tmax - trise))
    pulse[zero_mask] = 0
    return pulse

def real_pulse_with_noise(t):
    tmax = 6
    trise = 2.1287
    alpha = 1.0814
    pulse = np.power( (t-(tmax-trise))/trise, alpha ) * np.exp( -alpha*(t-tmax)/trise )
    zero_mask = np.where(t <= (tmax - trise))
    pulse[zero_mask] = 0
    noise = np.random.normal(loc=0, scale=0.1, size=num_samples) # add noise with standard deviation of 0.1
    pulse_with_noise = pulse + noise
    
    return pulse_with_noise

In [ ]:
# Generate the noise background
def noise(t):
    noise = np.random.normal(loc=0, scale=1, size=10)
    return noise


In [ ]:
def plot_timesamples(ax, time, emsignal_list, noisedata_list):
    #fig, ax = plt.subplots()
    for i, emsignal in enumerate(emsignal_list):
        noisedata = noisedata_list[i]
        ax.plot(time, emsignal, label=f'EM pulse' if i==1 else None, color='blue')
        ax.plot(time, noisedata, label=f'noise'  if i==1 else None,color='orange')
    ax.set_xlabel('Time (ns)')
    ax.set_ylabel('Amplitude (arb. units)')
    ax.legend()

In [ ]:
# Generate a dataset of real pulses
'''
t_events = np.zeros((num_events, num_samples))
X_real = np.zeros((num_events, num_samples))
y_real = np.zeros((num_events, 1))
X_noise = np.zeros((num_events, num_samples))
y_noise = np.zeros((num_events, 1))
for i in range(num_events):
    t_event = np.linspace(xmin, xmax, num_samples)
    t_events[i] = t_event
    pulse = real_pulse_with_noise(t_event) 
    #pulse = real_pulse(t_event) 
    X_real[i] = pulse
    y_real[i] = np.ones(1)# real pulse label
    
    X_noise[i] = np.random.normal(0, 1, size=num_samples)
    y_noise[i] = np.zeros(1)
    

print(X_real) 
print("Printing y_real")
print(y_real)
'''

#dirName = "noise_0p06/1GeV/"
#dirName = "noise_0p15/1GeV/"
#dirName = "noise_0p15/0p2GeV/"
dirName = "noise_0p15/0p15GeV/"

import uproot
### Energy = 10 GeV
# Open the ROOT file
#root_file = uproot.open(f"/eos/user/s/shilpi/SWAN_projects/ECAL_noise_EM_discrimination/data/{dirName}/outputPSWithoutPU_withNoise.root")
#root_file = uproot.open(f"/eos/user/s/shilpi/SWAN_projects/ECAL_noise_EM_discrimination/data/{dirName}/outputPSWithPU_withNoise.root")


### Energy = 1 GeV
#root_file = uproot.open(f"/eos/user/s/shilpi/SWAN_projects/ECAL_noise_EM_discrimination/data/{dirName}/outputPSWithoutPU_withNoise.root")
root_file = uproot.open(f"/eos/user/s/shilpi/SWAN_projects/ECAL_noise_EM_discrimination/data/{dirName}/outputPSWithPU_withNoise.root")
#root_file = uproot.open(f"/eos/user/d/dasgupsu/SWAN_projects/ECAL_noise_EM_discrimination/data/outputPSWithNoPU_withNoise_0.150000_0.15_v1.root")

# Access the tree containing the data
tree = root_file["Samples"]

# Read the needed branches into numpy arrays
arrays = tree.arrays(["samples", "ysamples","samplesNoise","ysamplesNoise" ])

# Read the "sample" and "sampleNoise" branches into numpy arrays
X_real = ak.to_numpy(arrays["samples"])
y_real = ak.to_numpy(arrays["ysamples"])
X_noise = ak.to_numpy(arrays["samplesNoise"])
y_noise = ak.to_numpy(arrays["ysamplesNoise"])

print(X_real) 
print("Printing y_real")
print(y_real)

data = np.concatenate([X_real, X_noise]) ### makes it [2*num_events,num_samples]
labels = np.concatenate([y_real,y_noise])


# Shuffle data and labels together
## Important to shuffle since I take some fraction of events so it should not happen that all the real events 
## are cluttered at the beginning
shuffle_indices = np.random.permutation(len(data))
data = data[shuffle_indices]
labels = labels[shuffle_indices]

###plot 
#fig, ax = plt.subplots()

'''
#ev_number = 4
ev_number = 100
ax = plot_timesamples(ax, t_events[ev_number], X_real[ev_number],X_noise[ev_number]) ###eventnumber
ev_number = 4
ax = plot_timesamples(ax, t_events[ev_number], X_real[ev_number],X_noise[ev_number]) ###eventnumber
'''

import awkward as ak

num_events = ak.num(X_real, axis=0)

###replace this block with actual time variable

t_events = np.zeros((num_events, num_samples))
for i in range(num_events):
    t_event = np.linspace(xmin, xmax, num_samples)
    t_events[i] = t_event
###replace this block with actual time variable

#fig, ax = plt.subplots()
ev_numbers = [1, 2, 3, 4, 5, 6, 7, 8, 9 , 10, 100, 200, 300]  # list of event numbers to plot
emsignal_list = [X_real[ev_number] for ev_number in ev_numbers]
noisedata_list = [X_noise[ev_number] for ev_number in ev_numbers]
#plot_timesamples(ax, t_events[ev_numbers[0]], emsignal_list, noisedata_list)
#plt.show()

In [ ]:
import awkward as ak

num_events_data = ak.num(data, axis=0)
print(f'number of rows in data is {num_events_data}')


ntimeSamples_data = ak.num(data, axis=1)
print(f'number of rows in data is {ntimeSamples_data[0]}') ## just take the 0th event

# Split into train and test sets
train_size = int(0.7 * num_events_data) ###times 2 because the noise is also in the same dataset, so it is 2*num_events
train_data = data[:train_size]
train_labels = labels[:train_size]
test_data = data[train_size:]
test_labels = labels[train_size:]

print(f'Size of training data is {train_size}')

'''
print(train_size)
print(train_data)
print(test_data)
'''

print(f'number of elements in data : training data : test data : {len(data)} : {len(train_data)} : {len(test_data)}')

In [ ]:
x_train = train_data
y_train = train_labels
#n_classes = len(np.unique(y_train))
x_test = test_data
y_test = test_labels

In [ ]:
x_train = x_train.reshape((x_train.shape[0], x_train.shape[1], 1))
x_test = x_test.reshape((x_test.shape[0], x_test.shape[1], 1))

In [ ]:
class Transformer(tf.keras.Model):

    def __init__(self, num_layers, embedding_dim, num_heads, fully_connected_dim, dropout_rate=0.1, layernorm_eps=1e-6):
        super(Transformer, self).__init__()

        self.encoder = Encoder(embedding_dim=embedding_dim,
                               num_heads=num_heads,
                               num_layers=num_layers,
                               fully_connected_dim=fully_connected_dim,
                               dropout_rate=dropout_rate,
                               layernorm_eps=layernorm_eps)
        self.pooling_layer = GlobalAveragePooling1D(data_format="channels_first")
        self.mlp_layers = Dense(128, activation="relu")
        self.dropout = Dropout(0.25)
        self.final_layer = Dense(1, activation='sigmoid')
        
    def call(self, inputs, training):
        enc_output = self.encoder(inputs, training)  # (batch_size, inp_seq_len, fully_connected_dim)
        pooling_output = self.pooling_layer(enc_output)
        #pooling_output = self.dropout(pooling_output)
        mlp_output = self.mlp_layers(pooling_output)
        final_output = self.final_layer(mlp_output) # (batch_size, tar_seq_len, target_vocab_size)
        #Encoder_model = keras.Model(inputs, enc_output)
        #Encoder_model.summary(expand_nested=True)
        return final_output

In [ ]:
class Encoder(tf.keras.layers.Layer):
  
    def __init__(self, embedding_dim,  num_heads, num_layers, fully_connected_dim,  dropout_rate=0.1, layernorm_eps=1e-6):
        super(Encoder, self).__init__()
        self.num_layers = num_layers
        self.embedding_dim = embedding_dim
        self.enc_layers = [EncoderLayer(embedding_dim=self.embedding_dim,
                                        num_heads=num_heads,
                                        fully_connected_dim=fully_connected_dim,
                                        dropout_rate=dropout_rate,
                                        layernorm_eps=layernorm_eps) 
                           for _ in range(self.num_layers)]

        self.dropout = Dropout(dropout_rate)
        
    def call(self, x, training):
        for i in range(self.num_layers):
            x = self.enc_layers[i](x, training)
        return x  # (batch_size, input_seq_len, fully_connected_dim)

In [ ]:
class EncoderLayer(tf.keras.layers.Layer):
    def __init__(self, embedding_dim, num_heads, fully_connected_dim, dropout_rate=0.1, layernorm_eps=1e-6):
        super(EncoderLayer, self).__init__()

        self.mha = MultiHeadAttention(num_heads=num_heads,
                                      key_dim=embedding_dim,
                                      dropout=dropout_rate)

        self.ffn = FullyConnected(embedding_dim=embedding_dim,
                                  fully_connected_dim=fully_connected_dim)

        self.layernorm1 = LayerNormalization(epsilon=layernorm_eps)
        self.layernorm2 = LayerNormalization(epsilon=layernorm_eps)

        self.dropout_ffn = Dropout(dropout_rate)
    
    def call(self, x, training):
        
        attn_output = self.mha(x, x) # Self attention (batch_size, input_seq_len, fully_connected_dim)
        
        out1 = self.layernorm1(x + attn_output)  # (batch_size, input_seq_len, fully_connected_dim)
        
        ffn_output = self.ffn(out1)  # (batch_size, input_seq_len, fully_connected_dim)
        
        #ffn_output =  self.dropout_ffn(ffn_output, training=training)
        encoder_layer_out = out1 + ffn_output
        #encoder_layer_out = self.layernorm2(out1 + ffn_output)  # (batch_size, input_seq_len, fully_connected_dim)
        
        return encoder_layer_out


In [ ]:
#def FullyConnected(embedding_dim, fully_connected_dim):
#    return tf.keras.Sequential([
#        tf.keras.layers.Dense(fully_connected_dim, activation='relu'),  # (batch_size, seq_len, dff)
#        tf.keras.layers.Dense(embedding_dim)  # (batch_size, seq_len, d_model)
#    ])

In [ ]:
def FullyConnected(embedding_dim, fully_connected_dim):
    return tf.keras.Sequential([
        tf.keras.layers.Conv1D(filters=fully_connected_dim, kernel_size=1, activation="relu"),  # (batch_size, seq_len, dff)
        tf.keras.layers.Conv1D(filters= 1, kernel_size=1)  # (batch_size, seq_len, d_model)
    ])

In [ ]:
input_shape = x_train.shape[1:]
inputs = keras.Input(shape=input_shape)
training = True
outputs = Transformer(num_layers = 4, embedding_dim = 256, num_heads = 4, fully_connected_dim = 4, dropout_rate=0.4, layernorm_eps=1e-6)(inputs, training)
model = keras.Model(inputs, outputs)
model.summary(expand_nested=True)
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
#model.compile(
#    loss="sparse_categorical_crossentropy",
#    optimizer=keras.optimizers.Adam(learning_rate=1e-4),
#    metrics=["sparse_categorical_accuracy"],
#)
history = model.fit(
    x_train,
    y_train,
    validation_split=0.2,
    epochs=200,
    batch_size=32
)
#model.save('/eos/user/s/shilpi/SWAN_projects/ECAL_noise_EM_discrimination/model/timeSeries_model.h5')

In [4]:
import numpy as np

def readucr(filename):
    data = np.loadtxt(filename, delimiter="\t")
    y = data[:, 0]
    x = data[:, 1:]
    return x, y.astype(int)


root_url = "https://raw.githubusercontent.com/hfawaz/cd-diagram/master/FordA/"

x_train, y_train = readucr(root_url + "FordA_TRAIN.tsv")
x_test, y_test = readucr(root_url + "FordA_TEST.tsv")

x_train = x_train.reshape((x_train.shape[0], x_train.shape[1], 1))
x_test = x_test.reshape((x_test.shape[0], x_test.shape[1], 1))

n_classes = len(np.unique(y_train))

idx = np.random.permutation(len(x_train))
x_train = x_train[idx]
y_train = y_train[idx]

y_train[y_train == -1] = 0
y_test[y_test == -1] = 0

In [ ]:
#y_train

In [5]:
from tensorflow import keras
from tensorflow.keras import layers

In [8]:
def transformer_encoder(inputs, head_size, num_heads, ff_dim, dropout=0):
    # Normalization and Attention
    #x = layers.LayerNormalization(epsilon=1e-6)(inputs)
    x = layers.MultiHeadAttention(
        key_dim=head_size, num_heads=num_heads, dropout=dropout
    )(inputs, inputs)
    #x = layers.Dropout(dropout)(x)
    res = x + inputs

    # Feed Forward Part
    x = layers.LayerNormalization(epsilon=1e-6)(res)
    x = layers.Conv1D(filters=ff_dim, kernel_size=1, activation="relu")(x)
    #x = layers.Dropout(dropout)(x)
    x = layers.Conv1D(filters=inputs.shape[-1], kernel_size=1)(x)
    return x + res

In [9]:
def build_model(
    input_shape,
    head_size,
    num_heads,
    ff_dim,
    num_transformer_blocks,
    mlp_units,
    dropout=0,
    mlp_dropout=0,
):
    inputs = keras.Input(shape=input_shape)
    x = inputs
    for _ in range(num_transformer_blocks):
        x = transformer_encoder(x, head_size, num_heads, ff_dim, dropout)

    x = layers.GlobalAveragePooling1D(data_format="channels_first")(x)
    for dim in mlp_units:
        x = layers.Dense(dim, activation="relu")(x)
        #x = layers.Dropout(mlp_dropout)(x)
    outputs = layers.Dense(1, activation="sigmoid")(x)
    return keras.Model(inputs, outputs)


In [10]:
input_shape = x_train.shape[1:]

model = build_model(
    input_shape,
    head_size=256,
    num_heads=4,
    ff_dim=4,
    num_transformer_blocks=4,
    mlp_units=[128],
    mlp_dropout=0.4,
    dropout=0.25,
)

model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
#model.compile(
#    loss="sparse_categorical_crossentropy",
#    optimizer=keras.optimizers.Adam(learning_rate=1e-4),
#    metrics=["sparse_categorical_accuracy"],
#)
model.summary()

callbacks = [keras.callbacks.EarlyStopping(patience=10, restore_best_weights=True)]

model.fit(
    x_train,
    y_train,
    validation_split=0.2,
    epochs=200,
    batch_size=32,
    callbacks=callbacks,
)

model.evaluate(x_test, y_test, verbose=1)


Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 500, 1)]     0           []                               
                                                                                                  
 multi_head_attention (MultiHea  (None, 500, 1)      7169        ['input_1[0][0]',                
 dAttention)                                                      'input_1[0][0]']                
                                                                                                  
 tf.__operators__.add (TFOpLamb  (None, 500, 1)      0           ['multi_head_attention[0][0]',   
 da)                                                              'input_1[0][0]']                
                                                                                              

Epoch 3/200
90/90 [==============================] - 23s 260ms/step - loss: 0.3622 - accuracy: 0.8510 - val_loss: 0.5209 - val_accuracy: 0.7587
Epoch 4/200
90/90 [==============================] - 24s 265ms/step - loss: 0.2998 - accuracy: 0.8830 - val_loss: 0.4621 - val_accuracy: 0.8003
Epoch 5/200
90/90 [==============================] - 24s 267ms/step - loss: 0.2531 - accuracy: 0.8997 - val_loss: 0.4694 - val_accuracy: 0.7947
Epoch 6/200
41/90 [============>.................] - ETA: 12s - loss: 0.1721 - accuracy: 0.9367

KeyboardInterrupt: 

In [6]:
y_train = y_train.reshape((y_train.shape[0],1))
y_test = y_test.reshape((y_test.shape[0],1))

In [7]:
y_train

array([[1],
       [1],
       [1],
       ...,
       [1],
       [1],
       [0]])

In [1]:
import pathlib
import random
import string
import re
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.layers import TextVectorization

In [25]:
text_file = keras.utils.get_file(
    fname="spa-eng.zip",
    origin="http://storage.googleapis.com/download.tensorflow.org/data/spa-eng.zip",
    extract=True,
)
text_file = pathlib.Path(text_file).parent / "spa-eng" / "spa.txt"

In [26]:
with open(text_file) as f:
    lines = f.read().split("\n")[:-1]
text_pairs = []
for line in lines:
    eng, spa = line.split("\t")
    spa = "[start] " + spa + " [end]"
    text_pairs.append((eng, spa))

In [27]:
for _ in range(5):
    print(random.choice(text_pairs))

('Do you play the guitar?', '[start] ¿Tocáis la guitarra? [end]')
('I can still hear your voice.', '[start] Todavía puedo oír tu voz. [end]')
('It was stiflingly hot.', '[start] Era sofocantemente caliente. [end]')
('Tom, I want you to come with me.', '[start] Tom, quiero que vengas conmigo. [end]')
("You don't have to study theology to be a believer.", '[start] No se necesita estudiar teología para ser creyente. [end]')


In [28]:
random.shuffle(text_pairs)
num_val_samples = int(0.15 * len(text_pairs))
num_train_samples = len(text_pairs) - 2 * num_val_samples
train_pairs = text_pairs[:num_train_samples]
val_pairs = text_pairs[num_train_samples : num_train_samples + num_val_samples]
test_pairs = text_pairs[num_train_samples + num_val_samples :]

print(f"{len(text_pairs)} total pairs")
print(f"{len(train_pairs)} training pairs")
print(f"{len(val_pairs)} validation pairs")
print(f"{len(test_pairs)} test pairs")

118964 total pairs
83276 training pairs
17844 validation pairs
17844 test pairs


In [29]:
test_pairs

[('All I drank was coffee.', '[start] Todo lo que bebí fue café. [end]'),
 ("There's nothing inside.", '[start] No hay nada adentro. [end]'),
 ('Smile.', '[start] Sonríe. [end]'),
 ("It wasn't real.", '[start] No fue real. [end]'),
 ("I've got some problems.", '[start] Tengo problemas. [end]'),
 ('Tom was singing.', '[start] Tom estaba cantando. [end]'),
 ("I don't want your help.", '[start] No quiero tu ayuda. [end]'),
 ("Tom doesn't know his own strength.",
  '[start] Tom no conoce su propia fuerza. [end]'),
 ("You're great.", '[start] Eres estupendo. [end]'),
 ("Who's your favorite Disney character?",
  '[start] ¿Quién es tu personaje favorito de Disney? [end]'),
 ('There comes our teacher.', '[start] Ahí viene nuestro profesor. [end]'),
 ('There is one big difference.', '[start] Hay una gran diferencia. [end]'),
 ('He wanted to please the crowd.',
  '[start] Quería satisfacer a la multitud. [end]'),
 ('The ground floor was flooded.',
  '[start] La planta baja estaba inundada. [end]

In [30]:
strip_chars = string.punctuation + "¿"
strip_chars = strip_chars.replace("[", "")
strip_chars = strip_chars.replace("]", "")

vocab_size = 15000
sequence_length = 20
batch_size = 64


def custom_standardization(input_string):
    lowercase = tf.strings.lower(input_string)
    return tf.strings.regex_replace(lowercase, "[%s]" % re.escape(strip_chars), "")


eng_vectorization = TextVectorization(
    max_tokens=vocab_size, output_mode="int", output_sequence_length=sequence_length,
)
spa_vectorization = TextVectorization(
    max_tokens=vocab_size,
    output_mode="int",
    output_sequence_length=sequence_length + 1,
    standardize=custom_standardization,
)
train_eng_texts = [pair[0] for pair in train_pairs]
train_spa_texts = [pair[1] for pair in train_pairs]
eng_vectorization.adapt(train_eng_texts)
spa_vectorization.adapt(train_spa_texts)

In [31]:
eng_vectorization("I am Suman")

<tf.Tensor: shape=(20,), dtype=int64, numpy=
array([ 3, 93,  1,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,  0,
        0,  0,  0])>

In [32]:
def format_dataset(eng, spa):
    eng = eng_vectorization(eng)
    spa = spa_vectorization(spa)
    print("suman",spa.shape)
    return ({"encoder_inputs": eng, "decoder_inputs": spa[:, :-1],}, spa[:, 1:])


def make_dataset(pairs):
    eng_texts, spa_texts = zip(*pairs)
    eng_texts = list(eng_texts)
    spa_texts = list(spa_texts)
    dataset = tf.data.Dataset.from_tensor_slices((eng_texts, spa_texts))
    dataset = dataset.batch(batch_size)
    dataset = dataset.map(format_dataset)
    return dataset.shuffle(2048).prefetch(16).cache()


train_ds = make_dataset(train_pairs)
val_ds = make_dataset(val_pairs)

suman (None, 21)
suman (None, 21)


In [10]:
train_ds

<CacheDataset element_spec=({'encoder_inputs': TensorSpec(shape=(None, 3), dtype=tf.int64, name=None), 'decoder_inputs': TensorSpec(shape=(None, 3), dtype=tf.int64, name=None)}, TensorSpec(shape=(None, 3), dtype=tf.int64, name=None))>

In [11]:
for inputs, targets in train_ds.take(1):
    print(f'inputs["encoder_inputs"].shape: {inputs["encoder_inputs"].shape}')
    print(f'inputs["decoder_inputs"].shape: {inputs["decoder_inputs"].shape}')
    print(f"targets.shape: {targets.shape}")
    print("encoder-----",inputs["encoder_inputs"][:5])
    print("decoder-----",targets[:5])
    

inputs["encoder_inputs"].shape: (64, 3)
inputs["decoder_inputs"].shape: (64, 3)
targets.shape: (64, 3)
encoder----- tf.Tensor(
[[  32 1566   91]
 [   9  117    4]
 [   3  133   13]
 [   9   14 1111]
 [   6   73   38]], shape=(5, 3), dtype=int64)
decoder----- tf.Tensor(
[[  90   37 3211]
 [ 142   46   34]
 [ 170    5   66]
 [  21  138  362]
 [   8    7  118]], shape=(5, 3), dtype=int64)


2023-07-19 10:39:39.877581: W tensorflow/core/kernels/data/cache_dataset_ops.cc:768] The calling iterator did not fully read the dataset being cached. In order to avoid unexpected truncation of the dataset, the partially cached contents of the dataset  will be discarded. This can happen if you have an input pipeline similar to `dataset.cache().take(k).repeat()`. You should use `dataset.take(k).cache().repeat()` instead.


In [20]:
train_pairs

[('Why are you under the desk?',
  '[start] ¿Por qué estás abajo del escritorio? [end]'),
 ("It's perfectly understandable.",
  '[start] Es perfectamente comprensible. [end]'),
 ("I think I'm going mad.", '[start] Creo que me estoy volviendo loca. [end]'),
 ('I hope you like chocolate cake.',
  '[start] Espero que te guste la torta de chocolate. [end]'),
 ('She said that he was handsome.', '[start] Dijo que era guapo. [end]'),
 ("You'll find the house empty.",
  '[start] Vas a encontrar la casa vacía. [end]'),
 ('Do people drink tea in your country?',
  '[start] ¿La gente bebe té en tu país? [end]'),
 ('Your plan is a good one.', '[start] El tuyo es un buen plan. [end]'),
 ('What causes teeth grinding?',
  '[start] ¿Qué causa el rechinar de dientes? [end]'),
 ("I think he's an honest man.",
  '[start] Yo creo que él es un hombre honesto. [end]'),
 ('In our park, we have a nice slide for children to play on.',
  '[start] En nuestro parque, tenemos una magnífica chirristra para que los n

In [18]:
 eng_texts, spa_texts = zip(*train_pairs)

In [24]:
type(spa_texts)

list

In [23]:
eng_texts = list(eng_texts)
spa_texts = list(spa_texts)

In [25]:
eng_texts

['Why are you under the desk?',
 "It's perfectly understandable.",
 "I think I'm going mad.",
 'I hope you like chocolate cake.',
 'She said that he was handsome.',
 "You'll find the house empty.",
 'Do people drink tea in your country?',
 'Your plan is a good one.',
 'What causes teeth grinding?',
 "I think he's an honest man.",
 'In our park, we have a nice slide for children to play on.',
 'Why did Tom say that?',
 'Tests start next week.',
 'Are you joking?',
 'He accepted reluctantly.',
 'I left my jacket in the classroom.',
 'Need anything else?',
 'The red chair was set apart. It was special.',
 'Will you help me clean the room?',
 'She put all her jewels into a little red box.',
 'He fell off the horse.',
 'What does she do?',
 'The restaurant owner allowed her to take table scraps home to feed all of her dogs.',
 'I had a tennis match with him.',
 "That's my wife.",
 'Tom should be here any minute now.',
 "He's likely to pass the entrance examination.",
 'We sat in the center 

In [40]:
dataset = tf.data.Dataset.from_tensor_slices((eng_texts, spa_texts))

In [43]:
type(dataset)

tensorflow.python.data.ops.dataset_ops.TensorSliceDataset

In [32]:
for element in dataset:
  print(element[1])

tf.Tensor(b'[start] \xc2\xbfPor qu\xc3\xa9 est\xc3\xa1s abajo del escritorio? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Es perfectamente comprensible. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Creo que me estoy volviendo loca. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Espero que te guste la torta de chocolate. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Dijo que era guapo. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Vas a encontrar la casa vac\xc3\xada. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfLa gente bebe t\xc3\xa9 en tu pa\xc3\xads? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] El tuyo es un buen plan. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfQu\xc3\xa9 causa el rechinar de dientes? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Yo creo que \xc3\xa9l es un hombre honesto. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] En nuestro parque, tenemos una magn\xc3\xadfica chirristra para que

tf.Tensor(b'[start] Lo hice en la escuela. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom es un muchacho muy listo. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Pertenece al cuerpo diplom\xc3\xa1tico. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom era el compa\xc3\xb1ero de celda de John. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfPodemos hablar con Tom? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Ella no se dar\xc3\xa1 por vencido con facilidad. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Vente a comer con nosotros. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Siempre he querido conocerte. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Sega sol\xc3\xada fabricar consolas de videojuego hace mucho tiempo. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tiene m\xc3\xa1s de cien a\xc3\xb1os. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No entiendo nada de esto. [end]', shape=(), dtype=string)
tf.Tensor(b'[sta

tf.Tensor(b'[start] Tom pod\xc3\xada oler el desayuno cocin\xc3\xa1ndose en la cocina. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfEres un estudiante de instituto? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Su cara delataba sus sentimientos verdaderos. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Quiero que conozcas a mi nuevo amigo, Tom. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Acudieron en su ayuda. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Parece que no est\xc3\xa1s pasando un buen rato aqu\xc3\xad. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom entr\xc3\xb3 a la habitaci\xc3\xb3n sin golpear la puerta. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfPor qu\xc3\xa9 tengo que ir a la escuela? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfHay alguna ley aqu\xc3\xad acerca de cruzar imprudentemente? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfToca \xc3\xa9l el piano? [end]', shape=()

tf.Tensor(b'[start] Tom no tiene idea de d\xc3\xb3nde vive Mary. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfTodav\xc3\xada sientes algo por \xc3\xa9l? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Quisiera hablar con uno de vuestros invitados. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Las tasas de inter\xc3\xa9s a largo plazo se han disparado. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Envidio la amistad que tienen Tom y Mary. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Mi padre se est\xc3\xa1 quedando calvo. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Los opositores dicen que las cosechas gen\xc3\xa9ticamente modificadas pueden polinizar y da\xc3\xb1ar otras cosechas. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom no tiene plata. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom se ducha todos los d\xc3\xadas. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Dejalo entrar. [end]', shape=(), dtype=string)
tf.Te

tf.Tensor(b'[start] Tenemos un mont\xc3\xb3n. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Su carrera como periodista estaba lleno de logros distinguidos. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No te hemos visto en un tiempo. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfPuedo ir con \xc3\xa9l? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Pon las luces. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Ma\xc3\xb1ana har\xc3\xa1 bueno. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfEncontr\xc3\xb3 Tom lo que estaba buscando? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc3\x89l va a la biblioteca a leer libros. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Me gusta tu coche. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom tiene mucho en com\xc3\xban con Mary. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Parece que has tenido un d\xc3\xada ajetreado. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No

...

tf.Tensor(b'[start] Tengo una piedra en el zapato. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Dorm\xc3\xad nueve horas. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Es posible que trate de hacer eso. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No tengo ni idea de qu\xc3\xa9 est\xc3\xa1 originando el problema. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom cerr\xc3\xb3 la boca. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc3\x89l me pidi\xc3\xb3 permiso para usar el tel\xc3\xa9fono. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Hay que esperar el momento adecuado para bajar la palanca. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Estaba esperando una respuesta. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Todos lo quieren. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfViste a alguien m\xc3\xa1s? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Pasaron muchas cosas injustas. [end]', shape=(), dtype=string)
tf.

tf.Tensor(b'[start] \xc2\xbfCu\xc3\xa1ndo fue la \xc3\xbaltima vez que perdiste tus llaves? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Soy mujer. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Esas fueron las horas m\xc3\xa1s tristes de mi vida. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom y Mary son buenos amigos. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc3\x89l tiene que seguir mi consejo. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Sab\xc3\xa9s donde encontrarme si quer\xc3\xa9s hablar. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Lo pill\xc3\xa9 intentando escabullirse. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Esta gente odia a todos los extranjeros. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Que se levante el acusado. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Ahora estoy preparado para irme. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfTodav\xc3\xada tiene ese libro que cogi\xc3\xb3 d

tf.Tensor(b'[start] No puedo ni mirarte. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No s\xc3\xa9 a ciencia cierta. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Mi hermana lo vio con sus propios ojos. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Esta silla est\xc3\xa1 rota. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Este me gusta a\xc3\xban m\xc3\xa1s. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Hoy es un d\xc3\xada soleado. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfRecibiste mi paquete? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] El sitio de acampada estaba totalmente desierto. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom ten\xc3\xada un arma. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Los gatos est\xc3\xa1n emparentados con los tigres. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfCu\xc3\xa1ntos colores hay? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfQu\xc3\xa9 opinas s

tf.Tensor(b'[start] Me voy a casar. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Me gustan las pel\xc3\xadculas. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom no tiene ganas de cocinar. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Nadie se ofrece voluntario. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom tiene un amplio c\xc3\xadrculo de amigos. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfDe qu\xc3\xa9 nos quieres proteger? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] La compa\xc3\xb1\xc3\xada rechaz\xc3\xb3 su solicitud de una transferencia. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] A\xc3\xb1ad\xc3\xad una habitaci\xc3\xb3n a mi casa. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No puedo culparos. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Lo har\xc3\xa9 como me aconsejas. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Espero que apruebe el examen f\xc3\xa1cilmente. [end]', shape=(), dtype=string)
t

tf.Tensor(b'[start] Hace mucho fr\xc3\xado aqu\xc3\xad. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] No creo que sea tan f\xc3\xa1cil. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Dame tu s\xc3\xa1ndwich. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Ahora da un paso atr\xc3\xa1s. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Estoy feliz de que todo ello terminara. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Soborn\xc3\xa9 al polic\xc3\xada. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Sus labios se encontraron. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfD\xc3\xb3nde est\xc3\xa1 Mar\xc3\xada? [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Tom olvid\xc3\xb3 firmar el cheque. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] Eso suena realmente interesante. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] El pescado sab\xc3\xada a salm\xc3\xb3n. [end]', shape=(), dtype=string)
tf.Tensor(b'[start] \xc2\xbfLa conoces desde

In [12]:
test_eng_texts = [pair[0] for pair in test_pairs]

In [16]:
test_eng_texts[0]

'Have you been there?'

In [18]:
eng_vectorization(test_eng_texts[0]).shape

TensorShape([20])

In [22]:
eng_vectorization([decoded_sentence]).shape

TensorShape([1, 20])

In [23]:
def decode_sequence(input_sentence):
    tokenized_input_sentence = eng_vectorization([input_sentence])
    decoded_sentence = "[start]"
    print(tokenized_input_sentence)
    return decoded_sentence


test_eng_texts = [pair[0] for pair in test_pairs]
for _ in range(30):
    input_sentence = random.choice(test_eng_texts)
    translated = decode_sequence(input_sentence)


tf.Tensor(
[[  6 214   7 138 503  99 398   0   0   0   0   0   0   0   0   0   0   0
    0   0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[   3   22   33    5    4 3219    0    0    0    0    0    0    0    0
     0    0    0    0    0    0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[  6 245 239   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[ 144 1666    0    0    0    0    0    0    0    0    0    0    0    0
     0    0    0    0    0    0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[  5  65 196  10  57  53 104   0   0   0   0   0   0   0   0   0   0   0
    0   0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[  3  14 771   4 353   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[ 13 273  36 381 233  95 634   0   0   0   0   0   0   0   0   0   0   0
    0   0]], shape=(1, 20), dtype=int64)
tf.Tensor(
[[  9 150  17  81 499   0   0   0   0   0   0   0   0   0   0   0  

In [33]:
train_ds

<CacheDataset element_spec=({'encoder_inputs': TensorSpec(shape=(None, 20), dtype=tf.int64, name=None), 'decoder_inputs': TensorSpec(shape=(None, 20), dtype=tf.int64, name=None)}, TensorSpec(shape=(None, 20), dtype=tf.int64, name=None))>